In [2]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "4" 
os.environ["WORLD_SIZE"] = "1"

In [3]:
import time
import torch
import gradio as gr
from diffusers import StableDiffusionPipeline, AutoencoderKL, ControlNetModel, StableDiffusionControlNetPipeline
from diffusers import DDPMScheduler, DEISMultistepScheduler, EulerAncestralDiscreteScheduler, DDIMScheduler, EulerDiscreteScheduler, HeunDiscreteScheduler

from PIL import Image

from ip_adapter import IPAdapterPlus, IPAdapter

/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2023-10-17 14:09:13.213394: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-10-17 14:09:18.049981: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [4]:
# def image_grid(imgs, rows, cols):
#     assert len(imgs) == rows*cols

#     w, h = imgs[0].size
#     grid = Image.new('RGB', size=(cols*w, rows*h))
#     grid_w, grid_h = grid.size
    
#     for i, img in enumerate(imgs):
#         grid.paste(img, box=(i%cols*w, i//cols*h))
#     return grid

# def init_pipe(base_model, ip_ckpt_path, vae_model_path, image_encoder_path, device, noise_sampler):
#     base_model = str(base_model)
#     noise_sampler = noise_sampler.from_pretrained(base_model, subfolder="scheduler")
#     print(f"{noise_sampler._class_name} was successfully loaded")
#     vae = AutoencoderKL.from_pretrained(str(vae_model_path)).to(dtype=torch.float16)
#     torch.cuda.empty_cache()
#     pipe = StableDiffusionPipeline.from_pretrained(
#         base_model,
#         torch_dtype=torch.float16,
#         scheduler=noise_sampler,
#         vae=vae,
#         feature_extractor=None,
#         safety_checker=None
#     )
#     # load ip-adapter
#     ip_model = IPAdapterPlus(pipe, image_encoder_path, str(ip_ckpt_path), device, num_tokens=16)
#     print(f"{base_model} was successfully loaded")

#     return ip_model


In [5]:
# def init_pipe(base_model, ip_ckpt_path, vae_model_path, image_encoder_path, device, noise_sampler):
#     base_model = str(base_model)
#     noise_sampler = noise_sampler.from_pretrained(base_model, subfolder="scheduler")
#     print(f"{noise_sampler._class_name} was successfully loaded")
#     vae = AutoencoderKL.from_pretrained(str(vae_model_path)).to(dtype=torch.float16)
#     torch.cuda.empty_cache()
#     pipe = StableDiffusionPipeline.from_pretrained(
#         base_model,
#         torch_dtype=torch.float16,
#         scheduler=noise_sampler,
#         vae=vae,
#         feature_extractor=None,
#         safety_checker=None
#     )
#     # load ip-adapter
#     ip_model = IPAdapterPlus(pipe, image_encoder_path, str(ip_ckpt_path), device, num_tokens=16)
#     print(f"{base_model} was successfully loaded")

#     return ip_model

def init_pipe(base_model, ip_ckpt_path, vae_model_path, image_encoder_path, device, noise_sampler, controlnet_model_path=None):
    torch.cuda.empty_cache()
    base_model = str(base_model)
    controlnet = ControlNetModel.from_pretrained(controlnet_model_path, torch_dtype=torch.float16) if controlnet_model_path is not None else None
    sd_pipeline = StableDiffusionControlNetPipeline if controlnet else StableDiffusionPipeline
    noise_sampler = noise_sampler.from_pretrained(base_model, subfolder="scheduler")
    
    print(f"{noise_sampler._class_name} was successfully loaded")


    vae = AutoencoderKL.from_pretrained(str(vae_model_path)).to(dtype=torch.float16)

    args = {
        "pretrained_model_name_or_path": base_model,
        "torch_dtype": torch.float16,
        "scheduler": noise_sampler,
        "vae": vae,
        "feature_extractor": None,
        "safety_checker": None,
    }

    if controlnet:
        args["controlnet"] = controlnet
    
    pipe = sd_pipeline.from_pretrained(**args)
    print(pipe)
    ip_adapt_cls = IPAdapterPlus if "plus" in ip_ckpt_path else IPAdapter
    num_tokens = 16 if "plus" in ip_ckpt_path else 4
    print(ip_adapt_cls)
    ip_model = ip_adapt_cls(pipe, image_encoder_path, str(ip_ckpt_path), device, num_tokens=num_tokens)
    print(f"{base_model} was successfully loaded")

    return ip_model


In [6]:
import numpy as np

def generate_image(ip_pipe, prompt, negative_prompt, pil_image, image=None, num_samples=4, height=512, width=512,
                           num_inference_steps=20, seed=42, scale=1.0, guidance_scale=7.5):
        torch.cuda.empty_cache()
        print(image)
        args = {
                "prompt":prompt, 
                "negative_prompt":negative_prompt, 
                "pil_image":pil_image, 
                "num_samples":int(num_samples), 
                "height":int(height), 
                "width":int(width),
                "num_inference_steps":int(num_inference_steps), 
                "seed":int(seed), 
                "scale":scale, 
                "guidance_scale":guidance_scale
            }

        if image is not None:
            print(image.size)
            args["image"] = image # [..., np.newaxis] #.transpose(1,2,0)[np.newaxis, ...]    
        images = ip_pipe.generate(**args)

        return images 

In [7]:
ip_dir = 'models/ip_adapters'
base_model_choices = [
    'Lykon/dreamshaper-8', 'runwayml/stable-diffusion-v1-5', 
    'dreamlike-art/dreamlike-anime-1.0','Lykon/AbsoluteReality',
    'SG161222/Realistic_Vision_V5.1_noVAE'
]

noise_sampler_dict = {
    "DDPM" : DDPMScheduler,
    "DEISMultiStep" : DEISMultistepScheduler,
    "DDIM" : DDIMScheduler,
    "Euler a" : EulerAncestralDiscreteScheduler,
    "Euler" : EulerDiscreteScheduler,
    "Heun" : HeunDiscreteScheduler,
}

sampler_choices = noise_sampler_dict.keys()

ip_choices = [os.path.join(ip_dir, f) for f in sorted(os.listdir(ip_dir)) if f]

prompt_examples = [
    ["A portrait of pretty person, smile, holding one cute dragon, as a beautiful fairy with glittering wings, decorations from outlandish stones, wearing a turtleneck decorated with glitter, nice even light, lofi, in a magical forest, digital art, trending on artstation, behance, deviantart, insanely detailed and intricate, many patterns",
    "dogs, wrinkled old face, cat, classic outfit, classic turtleneck, neckline, big breasts, enlarged breasts, big boobs, legs, closed eyes, deformed, distorted, disfigured, poorly drawn, bad anatomy, wrong anatomy, extra limb, missing limb, floating limbs, mutated hands and fingers, disconnected limbs, mutation, mutated, nudes, nude breasts, ugly, disgusting, blurry, amputation, unclear, bindi, pottu"],

    ["A person, high resolution, best quality, sharp focus, 8k, highly detailed, digital art, digital painting, trending art, smooth skin, detailed facial skin, symmetric",
    "blurry, unclear, low resolution, bad quality, nsfw, nudes, nude breasts, nude, shirtless, deformed iris, deformed pupils, mutated hands and fingers, nude, naked, deformed, distorted, disfigured, poorly drawn, bad anatomy, wrong anatomy, extra limb, missing limb, floating limbs, disconnected limbs, mutation, mutated, ugly, disgusting, amputation, closed eyes, big breasts, sign, mutated hands and fingers, bindi, pottu,"],
    ["high res"," low res"],

]

In [9]:
theme = gr.themes.Default(
    primary_hue="violet",
).set(
    button_secondary_background_fill='linear-gradient(to bottom right, *primary_100, *primary_300)'
)

with gr.Blocks(theme=theme) as demo:
    controlnet_dict = {
        "Openpose" : "lllyasviel/control_v11p_sd15_openpose",
        "Depth" : "lllyasviel/control_v11f1p_sd15_depth",
        "Canny" : "lllyasviel/control_v11p_sd15_canny"
        }

    vae_model_path = gr.State("stabilityai/sd-vae-ft-mse")
    image_encoder_path = gr.State("models/image_encoder/")
    ip_ckpt_path = gr.State("models/ip-adapter-plus-face_sd15.bin")
    device = gr.State('cuda') if torch.cuda.is_available() else gr.State('cpu')
    noise_scheduler = gr.State()
    img2 = gr.State()
    ip_pipe = gr.State()
    control_type = gr.State()

    gr.Markdown(
    """
    # IP-Adapter WebUI

    Choose base model, IP checkpoint, noise scheduler <br>
    Note: base model can be copied from huggingFace as a repo id <br>

    Define wehther or not to use ControlNet + its type (currently Depth (midas), OpenPose and Canny are supported). 
    Press "Load model". <br> <br>

    Load your image + add prompts (you can load recommended prompt from Example section, at bottom of the page). <br>
    Set the params as you wish, if you use controlNet load an image of preprocessor output (depth image / 2d openpose / canny) <br>
    + Generate image <br>

    See this [deck]("https://docs.google.com/presentation/d/1UzJDiC9SHOb7Ek2yFEPQwmAmVQDNVjM5XSIitDEiNc0/edit?usp=sharing") for more guidance.
    ENJOY!

    """)
    with gr.Column() as col:
        with gr.Row() as row:
            drop_base_model = gr.Dropdown(base_model_choices, allow_custom_value=True, label='Base Model', value="dreamlike-art/dreamlike-anime-1.0")
            drop_ip_ckpt = gr.Dropdown(ip_choices, allow_custom_value=False, label='IP ckpt', value="models/ip_adapters/ip-adapter-plus-face_sd15.bin")
            drop_nsampler = gr.Dropdown(sampler_choices, label='Noise Sampler', value="DDIM")
            control_cbox = gr.Checkbox(label='Use ControlNet', value=False)    
            radio_control = gr.Radio(list(controlnet_dict.keys()), label="ControlNet type", info="what kind of control-net do you want?", visible=False)
            
            btn_models = gr.Button(value='Load Model')
        with gr.Row() as row:
            txt1 = gr.Textbox(lines=1, max_lines=10, interactive=True, label="prompt")
            txt2 = gr.Textbox(lines=1, max_lines=10, interactive=True, label="negative prompt")
        with gr.Row() as row:
                img1 = gr.Image(height=300, width=300, image_mode='RGB',type='pil', label="Input image", show_label=True, tool='select', container=True)
                img_control = gr.Image(height=300, width=300, type='pil', visible=False, label='ControlNet image', interactive=True)
        with gr.Row() as row:
                btn2 = gr.Button(value="Generate Image")
        with gr.Row() as row:
                # output_img = gr.Image(label="Output image")
                output_img = gr.Gallery(label="Generated images", show_label=False, elem_id="gallery", rows=[2], object_fit="contain", height="auto", preview=False)                        
        with gr.Row() as row:   
            slider1 = gr.Slider(minimum=0, maximum=8, value=4, step=1, label="num samples")
            slider2 = gr.Slider(minimum=0, maximum=100, value=20, step=1, label='num steps')
            slider3 = gr.Slider(0, 1, value=0.7, label='scale')
            slider4 = gr.Slider(minimum=0, maximum=20, value=7.5, step=0.1, label='CFG')
            txt3 = gr.Textbox(value=512, label='height')
            txt4 = gr.Textbox(value=512, label='width')
            txt5 = gr.Textbox(value=42, label="seed")
        with gr.Row() as row:
            ex = gr.Examples(
            examples=prompt_examples,
            inputs=[txt1, txt2],
                    )
        
    def get_ip_pipe(input, ip_ckpt_path, vae_model_path, image_encoder_path, device, noise_scheduler, controlnet_path):
        print('Base model:', input)
        print('IP ckpt:', ip_ckpt_path)

        dict = {ip_pipe: init_pipe(input, ip_ckpt_path, vae_model_path, image_encoder_path, device, noise_scheduler, controlnet_path)}
        # btn2.update(interactive=True)
        return dict
    
    def get_controlnet_type(input):       
        return {control_type: controlnet_dict.get(input, None)}
    
    # lambda x: gr.Checkbox.update(value=x), inputs=control_cbox, outputs=control_cbox
    control_cbox.change(lambda x: gr.Checkbox.update(value=x), inputs=[control_cbox], outputs=[control_cbox]).then(lambda x: gr.Image.update(visible=x), inputs=control_cbox, outputs=img_control).then(lambda x: gr.Radio.update(visible=x), 
                                                                                                            inputs=control_cbox, outputs=radio_control).then(lambda x: {img2: x}, inputs=img_control, outputs=img2)

    radio_control.change(get_controlnet_type ,inputs=radio_control, outputs=control_type).then(lambda: gr.Button.update(interactive=True), inputs=[], outputs=btn2)

    drop_nsampler.change(lambda x: noise_sampler_dict[x] ,inputs=[drop_nsampler], outputs=[noise_scheduler]).then(
                            lambda: gr.Button.update(interactive=True), inputs=[], outputs=btn_models).then(
                            lambda: gr.Button.update(interactive=False), inputs=[], outputs=btn2)
    
    drop_base_model.change(lambda: gr.Button.update(interactive=True), inputs=[], outputs=btn_models)
    drop_ip_ckpt.change(lambda: gr.Button.update(interactive=True), inputs=[], outputs=btn_models)
    
    btn_models.click(lambda x: noise_sampler_dict[x] ,inputs=[drop_nsampler], outputs=[noise_scheduler]).then(lambda: gr.Button.update(interactive=False), inputs=[], outputs=btn2).then(
                            lambda: gr.Button.update(interactive=False), inputs=[], outputs=btn_models).then(
                                get_ip_pipe, inputs=[drop_base_model, drop_ip_ckpt, vae_model_path, image_encoder_path, device, noise_scheduler, control_type], outputs=[ip_pipe, output_img], 
                    show_progress=True).then(lambda: gr.Button.update(interactive=True), inputs=[], outputs=btn2)

    btn2.click(lambda x: {img2: x}, inputs=img_control, outputs=img2).then(
        fn=generate_image,
        inputs=[ip_pipe, txt1, txt2, 
                img1, img2,
                slider1 , txt3, txt4, 
                slider2, txt5, slider3, slider4],
        outputs=[output_img],
    )

demo.queue()
demo.launch(share=True)


Running on local URL:  http://127.0.0.1:7861
Running on public URL: https://30456c2767331a4c45.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


Base model: dreamlike-art/dreamlike-anime-1.0
IP ckpt: models/ip_adapters/ip-adapter-plus-face_sd15.bin


/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/diffusers/configuration_utils.py:134: FutureWarning: Accessing config attribute `_class_name` directly via 'DDIMScheduler' object attribute is deprecated. Please access '_class_name' over 'DDIMScheduler's config object instead, e.g. 'scheduler.config._class_name'.
  deprecate("direct config name access", "1.0.0", deprecation_message, standard_warn=False)


DDIMScheduler was successfully loaded


Loading pipeline components...: 100%|██████████| 5/5 [00:00<00:00,  6.50it/s]


...

/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/diffusers/pipelines/stable_diffusion/pipeline_stable_diffusion.py:237: FutureWarning: `_encode_prompt()` is deprecated and it will be removed in a future version. Use `encode_prompt()` instead. Also, be aware that the output format changed from a concatenated tensor to a tuple.
  deprecate("_encode_prompt()", "1.0.0", deprecation_message, standard_warn=False)
Traceback (most recent call last):
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/gradio/routes.py", line 439, in run_predict
    output = await app.get_blocks().process_api(
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/gradio/blocks.py", line 1389, in process_api
    result = await self.call_function(
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/gradio/blocks.py", line 1094, in call_function
    prediction = await anyio.to_thread.run_sync(
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/pyt

<PIL.Image.Image image mode=RGB size=3088x2320 at 0x7F5E7520B760>
(3088, 2320)


/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/diffusers/pipelines/stable_diffusion/pipeline_stable_diffusion.py:237: FutureWarning: `_encode_prompt()` is deprecated and it will be removed in a future version. Use `encode_prompt()` instead. Also, be aware that the output format changed from a concatenated tensor to a tuple.
  deprecate("_encode_prompt()", "1.0.0", deprecation_message, standard_warn=False)
Traceback (most recent call last):
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/gradio/routes.py", line 439, in run_predict
    output = await app.get_blocks().process_api(
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/gradio/blocks.py", line 1389, in process_api
    result = await self.call_function(
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/gradio/blocks.py", line 1094, in call_function
    prediction = await anyio.to_thread.run_sync(
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/pyt

<PIL.Image.Image image mode=RGB size=3088x2320 at 0x7F61A70DBA30>
(3088, 2320)


/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/diffusers/pipelines/stable_diffusion/pipeline_stable_diffusion.py:237: FutureWarning: `_encode_prompt()` is deprecated and it will be removed in a future version. Use `encode_prompt()` instead. Also, be aware that the output format changed from a concatenated tensor to a tuple.
  deprecate("_encode_prompt()", "1.0.0", deprecation_message, standard_warn=False)
Traceback (most recent call last):
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/gradio/routes.py", line 439, in run_predict
    output = await app.get_blocks().process_api(
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/gradio/blocks.py", line 1389, in process_api
    result = await self.call_function(
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/python3.10/site-packages/gradio/blocks.py", line 1094, in call_function
    prediction = await anyio.to_thread.run_sync(
  File "/fsx/homes/afruchtman/.envs/ms_env/lib/pyt